In [1]:
!pip install transformers  seqeval[gpu]

     |████████████████████████████████| 3.5 MB 5.2 MB/s 
     |████████████████████████████████| 43 kB 1.7 MB/s 
     |████████████████████████████████| 895 kB 29.2 MB/s 
     |████████████████████████████████| 6.8 MB 5.4 MB/s 
     |████████████████████████████████| 67 kB 3.1 MB/s 
     |████████████████████████████████| 596 kB 36.3 MB/s 
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16180 sha256=0ea999455854a307585dadfa3ab51d336f6b66f3ba3939c20d17e65f29700582
  Stored in directory: /root/.cache/pip/wheels/05/96/ee/7cac4e74f3b19e3158dce26a20a1c86b3533c43ec72a549fd7
Successfully built seqeval
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [2]:
import transformers

In [3]:
print(transformers.__version__)

4.16.2


In [59]:
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score, f1_score
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import BertTokenizerFast, BertConfig, BertForTokenClassification, AutoTokenizer, AutoModelForSequenceClassification

In [5]:
from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'
print(device)

cuda


In [6]:
# !conda install -y gdown

In [7]:
!gdown --id 1vOr1AIHbgkhTO9Ol9Jx5Wh98Qdyh1QKI

Downloading...
From: https://drive.google.com/uc?id=1vOr1AIHbgkhTO9Ol9Jx5Wh98Qdyh1QKI
To: /content/mr.tar.gz
100% 782k/782k [00:00<00:00, 76.8MB/s]


In [8]:
!ls

mr.tar.gz  sample_data


In [9]:
!tar -xvf mr.tar.gz

README.txt
wikiann-mr.bio


In [10]:
data = open("wikiann-mr.bio",'r').read().split('\n')

In [11]:
sentence = []
tag = []
sentence_temp = []
tag_temp = []
count = 0
check_str_1 = 'B-PER'
check_str_2 = 'B-LOC'
check_str_3 = 'B-ORG'

for i in range(0, len(data)):
  if(data[i]) == '':
    sentence.append(sentence_temp)
    tag.append(tag_temp)
    sentence_temp = []
    tag_temp = []
    count = count + 1
  else:
    sentence_temp.append(data[i].split()[0])
    temp = '\t'.join(data[i].split())
    res = check_str_1 in temp or check_str_2 in temp or check_str_3 in temp
    if(res):
      tag_temp.append(data[i].split()[6])
    else:
      tag_temp.append(data[i].split()[2])

In [12]:
print(sentence)

[['पुनर्निर्देशन', 'चंद्रशेखर', 'वेंकट', 'रामन'], ['येथे', 'सप्तशृंगी', 'देवीचे', 'देउळ', 'आहे', '.'], ['राष्ट्रपतिपदाच्या', 'निवडणुकीस', 'उभे', 'राहण्याअगोदर', 'यांनी', 'काँग्रेस', 'पक्षामधून', 'राजीनामा', 'दिला', '.'], ['पुनर्निर्देशन', 'गुरदयाल', 'सिंग', 'धिल्लन'], ['पुनर्निर्देशन', 'जॉन', 'जोसेफ', 'काल्डवेल', 'अॅबट'], ['पुनर्निर्देशन', 'एन.', 'जनार्दन', 'रेड्डी'], ['आपल्या', 'पित्याच्या', 'इच्छेप्रमाणे', 'तिने', 'विष्णूशी', 'लग्न', 'करता', 'शंकराला', 'वरले', '.'], ['पुनर्निर्देशन', 'ब्रिटिश', 'ईस्ट', 'इंडिया', 'कंपनी'], ['पुनर्निर्देशन', 'श्रीपाद', 'नारायण', 'पेंडसे'], ['हे', 'शहर', 'पुण्याचे', 'भगिनी', 'शहर', 'आहे', '.'], ['पुनर्निर्देशन', 'ब्रिटिश', 'ईस्ट', 'इंडिया', 'कंपनी'], ['पुनर्निर्देशन', 'पोप', 'युजीन', 'चौथा'], ['पुनर्निर्देशन', 'फिंसेंत', 'फान', 'घो'], ['जपान', 'मधे', 'राज्यकर्ता', 'हा', 'कधी', 'ही', 'त्याला', 'दिलेल्या', 'नावाने', 'संबोधिला', 'गेला', 'नाही', '.'], ['पुनर्निर्देशन', 'लिओनार्दो', 'दा', 'विंची'], ['पुनर्निर्देशन', 'चंद्रशेखर', 'वेंकट', 'रामन'], ['अमेरिकेती

In [13]:
print(tag)

[['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-ORG', 'I-ORG', 'O', 'O', 'O'], ['O', 'O', 'O', 'O', 'O', 'B-ORG', 'I-ORG', 'O', 'O', 'O'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'O'], ['O', 'B-ORG', 'I-ORG', 'I-ORG', 'I-ORG'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'O', 'B-LOC', 'O', 'O', 'O', 'O'], ['O', 'B-ORG', 'I-ORG', 'I-ORG', 'I-ORG'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['B-LOC', 'B-LOC', 'O', 'B-LOC', 'O', 'O', 'O', 'O', 'O'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-LOC', 'O', 'O', 'O', 'O', 'O', 'O', 'O'], ['O', 'O', 'O', 'B-ORG', 'I-ORG', 'O', 'O', 'O'], ['O', 'O', 'O', 'O', 'O', 'O', 'B-PER', 'I-PER', 'O', 'O'], ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', '

In [14]:
id = []

for i in range(0, len(sentence)):
  id.append(len(sentence[i]))

In [15]:
print(id)

[4, 6, 10, 4, 5, 4, 10, 5, 4, 7, 5, 4, 4, 13, 4, 4, 9, 4, 4, 9, 8, 10, 12, 9, 5, 7, 7, 4, 4, 5, 7, 4, 4, 5, 6, 6, 6, 7, 6, 6, 8, 6, 6, 8, 4, 4, 6, 4, 5, 4, 5, 12, 4, 7, 14, 10, 11, 4, 8, 14, 6, 5, 4, 4, 4, 10, 6, 8, 5, 5, 4, 5, 5, 4, 4, 5, 4, 5, 4, 5, 5, 5, 5, 12, 5, 6, 12, 19, 18, 5, 7, 7, 8, 4, 5, 6, 4, 4, 5, 4, 5, 4, 4, 4, 4, 4, 13, 9, 4, 13, 7, 4, 4, 4, 12, 11, 16, 4, 7, 11, 13, 4, 8, 14, 4, 11, 4, 5, 12, 12, 13, 22, 12, 4, 5, 21, 5, 5, 5, 5, 5, 6, 5, 4, 5, 5, 5, 5, 13, 29, 9, 4, 4, 8, 4, 4, 4, 4, 5, 6, 6, 5, 4, 8, 19, 4, 4, 4, 8, 9, 5, 11, 7, 7, 11, 8, 5, 7, 6, 5, 8, 6, 7, 13, 4, 4, 6, 4, 4, 4, 10, 15, 12, 7, 12, 9, 5, 5, 16, 13, 13, 4, 4, 4, 5, 3, 6, 9, 5, 5, 5, 5, 4, 5, 4, 8, 4, 5, 9, 11, 4, 4, 5, 4, 18, 5, 12, 23, 22, 4, 4, 7, 7, 12, 4, 4, 16, 9, 4, 15, 5, 4, 11, 4, 10, 9, 5, 11, 7, 6, 5, 11, 5, 18, 9, 17, 11, 9, 8, 4, 5, 5, 4, 5, 5, 5, 16, 4, 5, 4, 4, 5, 4, 4, 4, 4, 9, 9, 4, 4, 4, 11, 5, 5, 6, 4, 4, 5, 5, 9, 10, 4, 7, 9, 5, 8, 4, 17, 7, 4, 5, 4, 5, 5, 10, 6, 6, 4, 4, 4, 4, 4, 

In [16]:
id_list = []

for i in range(0, len(sentence)):
  id_temp = ['Sentence: ' + str(i+1)] * id[i]
  id_list.append(id_temp)

In [17]:
print(id_list)

[['Sentence: 1', 'Sentence: 1', 'Sentence: 1', 'Sentence: 1'], ['Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2'], ['Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3', 'Sentence: 3'], ['Sentence: 4', 'Sentence: 4', 'Sentence: 4', 'Sentence: 4'], ['Sentence: 5', 'Sentence: 5', 'Sentence: 5', 'Sentence: 5', 'Sentence: 5'], ['Sentence: 6', 'Sentence: 6', 'Sentence: 6', 'Sentence: 6'], ['Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7', 'Sentence: 7'], ['Sentence: 8', 'Sentence: 8', 'Sentence: 8', 'Sentence: 8', 'Sentence: 8'], ['Sentence: 9', 'Sentence: 9', 'Sentence: 9', 'Sentence: 9'], ['Sentence: 10', 'Sentence: 10', 'Sentence: 10', 'Sentence: 10', 'Sentence: 10', 'Sentence: 10', 'Sentence: 10'], ['Sentence: 11', 'Sentence: 11', 'Sentence: 11', 'Sentence: 11', 'Sentence: 11'], ['Sen

In [18]:
print(sentence[:10])
print(tag[:10])
print(id_list[:10])

[['पुनर्निर्देशन', 'चंद्रशेखर', 'वेंकट', 'रामन'], ['येथे', 'सप्तशृंगी', 'देवीचे', 'देउळ', 'आहे', '.'], ['राष्ट्रपतिपदाच्या', 'निवडणुकीस', 'उभे', 'राहण्याअगोदर', 'यांनी', 'काँग्रेस', 'पक्षामधून', 'राजीनामा', 'दिला', '.'], ['पुनर्निर्देशन', 'गुरदयाल', 'सिंग', 'धिल्लन'], ['पुनर्निर्देशन', 'जॉन', 'जोसेफ', 'काल्डवेल', 'अॅबट'], ['पुनर्निर्देशन', 'एन.', 'जनार्दन', 'रेड्डी'], ['आपल्या', 'पित्याच्या', 'इच्छेप्रमाणे', 'तिने', 'विष्णूशी', 'लग्न', 'करता', 'शंकराला', 'वरले', '.'], ['पुनर्निर्देशन', 'ब्रिटिश', 'ईस्ट', 'इंडिया', 'कंपनी'], ['पुनर्निर्देशन', 'श्रीपाद', 'नारायण', 'पेंडसे'], ['हे', 'शहर', 'पुण्याचे', 'भगिनी', 'शहर', 'आहे', '.']]
[['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-ORG', 'I-ORG', 'O', 'O', 'O'], ['O', 'O', 'O', 'O', 'O', 'B-ORG', 'I-ORG', 'O', 'O', 'O'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER', 'I-PER'], ['O', 'B-PER', 'I-PER', 'I-PER'], ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-ORG', 'O', 'O'], ['O', 'B-ORG', 'I-ORG', 'I-ORG', 'I-ORG'], ['O', 'B-PER', 'I-PE

In [19]:
def flatten(t):
    return [item for sublist in t for item in sublist]

In [20]:
flat_sentence = flatten(sentence)
flat_tag = flatten(tag)
flat_id_list = flatten(id_list)

In [21]:
print(len(flat_sentence))
print(len(flat_tag))
print(len(flat_id_list))

108579
108579
108579


In [22]:
print(flat_sentence[:10])
print(flat_tag[:10])
print(flat_id_list[:10])

['पुनर्निर्देशन', 'चंद्रशेखर', 'वेंकट', 'रामन', 'येथे', 'सप्तशृंगी', 'देवीचे', 'देउळ', 'आहे', '.']
['O', 'B-PER', 'I-PER', 'I-PER', 'O', 'B-ORG', 'I-ORG', 'O', 'O', 'O']
['Sentence: 1', 'Sentence: 1', 'Sentence: 1', 'Sentence: 1', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2']


In [23]:
data_list = []
data_list.append(flat_id_list)
data_list.append(flat_sentence)
data_list.append(flat_tag)

In [24]:
print(data_list[0][:10])
print(data_list[1][:10])
print(data_list[2][:10])

['Sentence: 1', 'Sentence: 1', 'Sentence: 1', 'Sentence: 1', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2', 'Sentence: 2']
['पुनर्निर्देशन', 'चंद्रशेखर', 'वेंकट', 'रामन', 'येथे', 'सप्तशृंगी', 'देवीचे', 'देउळ', 'आहे', '.']
['O', 'B-PER', 'I-PER', 'I-PER', 'O', 'B-ORG', 'I-ORG', 'O', 'O', 'O']


In [25]:
data = pd.DataFrame(list(zip(flat_id_list, flat_sentence, flat_tag)), columns = ['Sentence #', 'Word', 'Tag'])

In [26]:
data

Sentence #           Word    Tag
0           Sentence: 1  पुनर्निर्देशन      O
1           Sentence: 1      चंद्रशेखर  B-PER
2           Sentence: 1          वेंकट  I-PER
3           Sentence: 1           रामन  I-PER
4           Sentence: 2           येथे      O
...                 ...            ...    ...
108574  Sentence: 14978  पुनर्निर्देशन      O
108575  Sentence: 14978         महानगर  B-ORG
108576  Sentence: 14978        टेलिफोन  I-ORG
108577  Sentence: 14978           निगम  I-ORG
108578  Sentence: 14978        लिमिटेड  I-ORG

[108579 rows x 3 columns]

In [27]:
data.count()

Sentence #    108579
Word          108579
Tag           108579
dtype: int64

In [28]:
print("Number of tags: {}".format(len(data.Tag.unique())))
frequencies = data.Tag.value_counts()
frequencies

Number of tags: 7


O        65645
I-ORG    10123
I-PER     9706
B-LOC     8320
B-PER     6120
I-LOC     4349
B-ORG     4316
Name: Tag, dtype: int64

In [29]:
tags = {}
for tag, count in zip(frequencies.index, frequencies):
    if tag != "O":
        if tag[2:5] not in tags.keys():
            tags[tag[2:5]] = count
        else:
            tags[tag[2:5]] += count
    continue

print(sorted(tags.items(), key=lambda x: x[1], reverse=True))

[('PER', 15826), ('ORG', 14439), ('LOC', 12669)]


In [30]:
labels_to_ids = {k: v for v, k in enumerate(data.Tag.unique())}
ids_to_labels = {v: k for v, k in enumerate(data.Tag.unique())}
labels_to_ids

{'B-LOC': 5,
 'B-ORG': 3,
 'B-PER': 1,
 'I-LOC': 6,
 'I-ORG': 4,
 'I-PER': 2,
 'O': 0}

In [31]:
# let's create a new column called "sentence" which groups the words by sentence 
data['sentence'] = data[['Sentence #','Word','Tag']].groupby(['Sentence #'])['Word'].transform(lambda x: ' '.join(x))
# let's also create a new column called "word_labels" which groups the tags by sentence 
data['word_labels'] = data[['Sentence #','Word','Tag']].groupby(['Sentence #'])['Tag'].transform(lambda x: ','.join(x))
data.head()

Sentence #  ...          word_labels
0  Sentence: 1  ...  O,B-PER,I-PER,I-PER
1  Sentence: 1  ...  O,B-PER,I-PER,I-PER
2  Sentence: 1  ...  O,B-PER,I-PER,I-PER
3  Sentence: 1  ...  O,B-PER,I-PER,I-PER
4  Sentence: 2  ...  O,B-ORG,I-ORG,O,O,O

[5 rows x 5 columns]

In [32]:
data = data[["sentence", "word_labels"]].drop_duplicates().reset_index(drop=True)
data.head()

sentence                  word_labels
0                 पुनर्निर्देशन चंद्रशेखर वेंकट रामन          O,B-PER,I-PER,I-PER
1                   येथे सप्तशृंगी देवीचे देउळ आहे .          O,B-ORG,I-ORG,O,O,O
2  राष्ट्रपतिपदाच्या निवडणुकीस उभे राहण्याअगोदर य...  O,O,O,O,O,B-ORG,I-ORG,O,O,O
3                  पुनर्निर्देशन गुरदयाल सिंग धिल्लन          O,B-PER,I-PER,I-PER
4              पुनर्निर्देशन जॉन जोसेफ काल्डवेल अॅबट    O,B-PER,I-PER,I-PER,I-PER

In [33]:
len(data)

10835

In [34]:
data.iloc[41].sentence

'पुनर्निर्देशन योसिफ ब्रोझ तितो'

In [35]:
data.iloc[41].word_labels

'O,B-PER,I-PER,I-PER'

In [71]:
MAX_LEN = 128
TRAIN_BATCH_SIZE = 16
VALID_BATCH_SIZE = 16
EPOCHS = 1
LEARNING_RATE = 1e-05
MAX_GRAD_NORM = 10
tokenizer = BertTokenizerFast.from_pretrained('bert-base-multilingual-cased')

In [72]:
class dataset(Dataset):
  def __init__(self, dataframe, tokenizer, max_len):
        self.len = len(dataframe)
        self.data = dataframe
        self.tokenizer = tokenizer
        self.max_len = max_len

  def __getitem__(self, index):
        # step 1: get the sentence and word labels 
        sentence = self.data.sentence[index].strip().split()  
        word_labels = self.data.word_labels[index].split(",") 

        # step 2: use tokenizer to encode sentence (includes padding/truncation up to max length)
        # BertTokenizerFast provides a handy "return_offsets_mapping" functionality for individual tokens
        encoding = self.tokenizer(sentence,
                             is_split_into_words=True,
                             return_offsets_mapping=True, 
                             padding='max_length', 
                             truncation=True, 
                             max_length=self.max_len)
        
        # step 3: create token labels only for first word pieces of each tokenized word
        labels = [labels_to_ids[label] for label in word_labels] 
        # code based on https://huggingface.co/transformers/custom_datasets.html#tok-ner
        # create an empty array of -100 of length max_length
        encoded_labels = np.ones(len(encoding["offset_mapping"]), dtype=int) * -100
        
        # set only labels whose first offset position is 0 and the second is not 0
        i = 0
        for idx, mapping in enumerate(encoding["offset_mapping"]):
          if mapping[0] == 0 and mapping[1] != 0:
            # overwrite label
            encoded_labels[idx] = labels[i]
            i += 1

        # step 4: turn everything into PyTorch tensors
        item = {key: torch.as_tensor(val) for key, val in encoding.items()}
        item['labels'] = torch.as_tensor(encoded_labels)
        
        return item

  def __len__(self):
        return self.len

In [73]:
train_size = 0.7 
train_dataset = data.sample(frac=train_size,random_state=200)
test_dataset = data.drop(train_dataset.index).reset_index(drop=True)
train_dataset = train_dataset.reset_index(drop=True)

print("FULL Dataset: {}".format(data.shape))
print("TRAIN Dataset: {}".format(train_dataset.shape))
print("TEST Dataset: {}".format(test_dataset.shape))

training_set = dataset(train_dataset, tokenizer, MAX_LEN)
testing_set = dataset(test_dataset, tokenizer, MAX_LEN)

FULL Dataset: (10835, 2)
TRAIN Dataset: (7584, 2)
TEST Dataset: (3251, 2)


In [74]:
training_set[0]

{'attention_mask': tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0]),
 'input_ids': tensor([  101,   885, 65430,   887, 39800, 49709, 13671, 25695,   885, 14018,
         27694, 31277, 28960,   113, 84293, 22649, 22852,   100, 84293, 21897,
         21897,   114,   102,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     0,     0,     0,     0,
             0,     0,     0,     0,     0,     0,     

In [75]:
for token, label in zip(tokenizer.convert_ids_to_tokens(training_set[0]["input_ids"]), training_set[0]["labels"]):
  print('{0:10}  {1}'.format(token, label))

[CLS]       -100
प           1
##ोप        -100
ब           2
##ेन        -100
##ेड        -100
##िक        -100
##्ट        -100
प           2
##ं         -100
##ध         -100
##रा        -100
##वा        -100
(           0
१९          0
##१         -100
##४         -100
[UNK]       -100
१९          -100
##२         -100
##२         -100
)           0
[SEP]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -100
[PAD]       -10

In [76]:
train_params = {'batch_size': TRAIN_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

test_params = {'batch_size': VALID_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

training_loader = DataLoader(training_set, **train_params)
testing_loader = DataLoader(testing_set, **test_params)

In [77]:
model = BertForTokenClassification.from_pretrained('bert-base-multilingual-cased', num_labels=len(labels_to_ids))
model.to(device)

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForTokenClassification: ['cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForTokenClassification were not initialized from the model checkpoint at 

BertForTokenClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwi

In [43]:
inputs = training_set[2]
input_ids = inputs["input_ids"].unsqueeze(0)
attention_mask = inputs["attention_mask"].unsqueeze(0)
labels = inputs["labels"].unsqueeze(0)

input_ids = input_ids.to(device)
attention_mask = attention_mask.to(device)
labels = labels.to(device)

outputs = model(input_ids, attention_mask=attention_mask, labels=labels)
initial_loss = outputs[0]
initial_loss

tensor(1.7948, device='cuda:0', grad_fn=<NllLossBackward0>)

In [44]:
tr_logits = outputs[1]
tr_logits.shape

torch.Size([1, 128, 7])

In [45]:
optimizer = torch.optim.Adam(params=model.parameters(), lr=LEARNING_RATE)

In [48]:
# Defining the training function on the 80% of the dataset for tuning the bert model
def train(epoch):
    tr_loss, tr_accuracy = 0, 0
    nb_tr_examples, nb_tr_steps = 0, 0
    tr_preds, tr_labels = [], []
    # put model in training mode
    model.train()
    
    for idx, batch in enumerate(training_loader):
        
        ids = batch['input_ids'].to(device, dtype = torch.long)
        mask = batch['attention_mask'].to(device, dtype = torch.long)
        labels = batch['labels'].to(device, dtype = torch.long)

        loss, tr_logits = model(input_ids=ids, attention_mask=mask, labels=labels, return_dict=False)
        # print(model(input_ids=ids, attention_mask=mask, labels=labels))
        # print(type(loss))
        # loss
        # print(type(tr_logits))
        # print(tr_logits)        
        tr_loss += loss.item()

        nb_tr_steps += 1
        nb_tr_examples += labels.size(0)
        
        if idx % 100==0:
            loss_step = tr_loss/nb_tr_steps
            print(f"Training loss per 100 training steps: {loss_step}")
           
        # compute training accuracy
        flattened_targets = labels.view(-1) # shape (batch_size * seq_len,)
        active_logits = tr_logits.view(-1, model.num_labels) # shape (batch_size * seq_len, num_labels)
        flattened_predictions = torch.argmax(active_logits, axis=1) # shape (batch_size * seq_len,)
        
        # only compute accuracy at active labels
        active_accuracy = labels.view(-1) != -100 # shape (batch_size, seq_len)
        #active_labels = torch.where(active_accuracy, labels.view(-1), torch.tensor(-100).type_as(labels))
        
        labels = torch.masked_select(flattened_targets, active_accuracy)
        predictions = torch.masked_select(flattened_predictions, active_accuracy)
        
        tr_labels.extend(labels)
        tr_preds.extend(predictions)

        tmp_tr_accuracy = accuracy_score(labels.cpu().numpy(), predictions.cpu().numpy())
        tr_accuracy += tmp_tr_accuracy
    
        # gradient clipping
        torch.nn.utils.clip_grad_norm_(
            parameters=model.parameters(), max_norm=MAX_GRAD_NORM
        )
        
        # backward pass
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    epoch_loss = tr_loss / nb_tr_steps
    tr_accuracy = tr_accuracy / nb_tr_steps
    print(f"Training loss epoch: {epoch_loss}")
    print(f"Training accuracy epoch: {tr_accuracy}")

In [49]:
for epoch in range(EPOCHS):
    print(f"Training epoch: {epoch + 1}")
    train(epoch)

Training epoch: 1
Training loss per 100 training steps: 1.9061615467071533
Training loss per 100 training steps: 0.7170523198524325
Training loss per 100 training steps: 0.5117946513997975
Training loss per 100 training steps: 0.42760253408026455
Training loss per 100 training steps: 0.3803832831413966
Training loss epoch: 0.3573023464436395
Training accuracy epoch: 0.8900050877232476


In [50]:
def valid(model, testing_loader):
    # put model in evaluation mode
    model.eval()
    
    eval_loss, eval_accuracy = 0, 0
    nb_eval_examples, nb_eval_steps = 0, 0
    eval_preds, eval_labels = [], []
    
    with torch.no_grad():
        for idx, batch in enumerate(testing_loader):
            
            ids = batch['input_ids'].to(device, dtype = torch.long)
            mask = batch['attention_mask'].to(device, dtype = torch.long)
            labels = batch['labels'].to(device, dtype = torch.long)
            
            loss, eval_logits = model(input_ids=ids, attention_mask=mask, labels=labels, return_dict=False)
            
            eval_loss += loss.item()

            nb_eval_steps += 1
            nb_eval_examples += labels.size(0)
        
            if idx % 100==0:
                loss_step = eval_loss/nb_eval_steps
                print(f"Validation loss per 100 evaluation steps: {loss_step}")
              
            # compute evaluation accuracy
            flattened_targets = labels.view(-1) # shape (batch_size * seq_len,)
            active_logits = eval_logits.view(-1, model.num_labels) # shape (batch_size * seq_len, num_labels)
            flattened_predictions = torch.argmax(active_logits, axis=1) # shape (batch_size * seq_len,)
            
            # only compute accuracy at active labels
            active_accuracy = labels.view(-1) != -100 # shape (batch_size, seq_len)
        
            labels = torch.masked_select(flattened_targets, active_accuracy)
            predictions = torch.masked_select(flattened_predictions, active_accuracy)
            
            eval_labels.extend(labels)
            eval_preds.extend(predictions)
            
            tmp_eval_accuracy = accuracy_score(labels.cpu().numpy(), predictions.cpu().numpy())
            eval_accuracy += tmp_eval_accuracy

    labels = [ids_to_labels[id.item()] for id in eval_labels]
    predictions = [ids_to_labels[id.item()] for id in eval_preds]
    
    eval_loss = eval_loss / nb_eval_steps
    eval_accuracy = eval_accuracy / nb_eval_steps
    print(f"Validation Loss: {eval_loss}")
    print(f"Validation Accuracy: {eval_accuracy}")

    return labels, predictions

In [51]:
labels, predictions = valid(model, testing_loader)

Validation loss per 100 evaluation steps: 0.08192114531993866
Validation loss per 100 evaluation steps: 0.20513465609585885
Validation loss per 100 evaluation steps: 0.20026513787718556
Validation Loss: 0.20272559564852832
Validation Accuracy: 0.9363244918773296


In [53]:
labels

['O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'I-PER',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'I-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'I-LOC',
 'I-LOC',
 'O',
 'B-PER',
 'I-PER',
 'I-PER',
 'I-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-ORG',
 'I-ORG',
 'I-ORG',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'B-PER',
 'I-PER',
 'B-PER',
 'I-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 '

In [54]:
predictions

['O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'I-PER',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'I-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'I-LOC',
 'I-LOC',
 'O',
 'B-PER',
 'I-PER',
 'I-PER',
 'I-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-ORG',
 'I-ORG',
 'I-ORG',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'B-PER',
 'I-PER',
 'B-PER',
 'I-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-PER',
 'I-PER',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-LOC',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',


In [56]:
# from seqeval.metrics import classification_report

# print(classification_report(labels, predictions))

f1_score(labels, predictions, average='macro')

0.8631333746657475